<a href="https://colab.research.google.com/github/KEERTHI-357/game-_analytics/blob/main/Untitled2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# importing needed libraries
import requests
import json
url = "https://api.sportradar.com/tennis/trial/v3/en/competitions.json"

headers = {
    "accept": "application/json",
    "x-api-key": "iaTuGgBk0r1GXdd3bIyvQOvEb5uYq0I7fmYiATOl"
}

response = requests.get(url, headers=headers)

print(response.text)

# converting the json data into python dictionary
data = json.loads(response.text)
# extracting data
competitions = data['competitions']

# extracting the competition details
competitions_list = []
for comp in competitions:
        competitions_list.append({
            'id': comp['id'],
            'name': comp['name'],
            'type': comp['type'],
            'gender': comp['gender']
        })

# extracting category details and removing duplicates
category_list = []
for comp in competitions:
        category_list.append({
            'category_id': comp['category']['id'],
            'category_name': comp['category']['name'],
        })

unique_categories = {frozenset(cat.items()): cat for cat in category_list}.values()

# printing results for verification
print('Competitions list:')
for comp in competitions_list:
        print(comp)

print('\nUnique categories list:')
for cat in unique_categories:
        print(cat)
# converting it into a dataframe
import pandas as pd
competitions_df = pd.DataFrame(competitions_list)
categories_df = pd.DataFrame(unique_categories)
competitions_df.head()
categories_df.head()





{"generated_at":"2025-09-02T09:08:31+00:00","competitions":[{"id":"sr:competition:620","name":"Hopman Cup","type":"mixed","gender":"mixed","category":{"id":"sr:category:181","name":"Hopman Cup"}},{"id":"sr:competition:660","name":"World Team Cup","type":"mixed","gender":"men","category":{"id":"sr:category:3","name":"ATP"},"level":"atp_250"},{"id":"sr:competition:990","name":"ATP Challenger Tour Finals","parent_id":"sr:competition:6239","type":"singles","gender":"men","category":{"id":"sr:category:72","name":"Challenger"}},{"id":"sr:competition:1207","name":"Championship International Series","type":"singles","gender":"women","category":{"id":"sr:category:6","name":"WTA"},"level":"wta_championships"},{"id":"sr:competition:2100","name":"Davis Cup","type":"mixed","gender":"men","category":{"id":"sr:category:76","name":"Davis Cup"}},{"id":"sr:competition:2102","name":"Billie Jean King Cup","type":"mixed","gender":"women","category":{"id":"sr:category:74","name":"Billie Jean King Cup"}},{"i

category_id category_name
0  sr:category:181    Hopman Cup
1    sr:category:3           ATP
2   sr:category:72    Challenger
3    sr:category:6           WTA
4   sr:category:76     Davis Cup

In [ ]:
import sqlite3

# Create  SQLite database
conn = sqlite3.connect(":memory:")
cursor = conn.cursor()

# Creating Categories table
cursor.execute("""
CREATE TABLE Categories (
    category_id VARCHAR(50) PRIMARY KEY,
    category_name VARCHAR(100) NOT NULL
);
""")

# Create Competitions table
cursor.execute("""
CREATE TABLE Competitions (
    competition_id VARCHAR(50) PRIMARY KEY,
    competition_name VARCHAR(100) NOT NULL,
    parent_id VARCHAR(50),
    type VARCHAR(20),
    gender VARCHAR(20),
    category_id VARCHAR(50),
    FOREIGN KEY (category_id) REFERENCES Categories(category_id)
);
""")


# Inserting values into the categories table
for comp in competitions:
    cursor.execute(
        "INSERT OR IGNORE INTO Categories (category_id, category_name) VALUES (?, ?)",
        (comp['category']['id'], comp['category']['name'])
    )

# Inserting values into the competitions table
for comp in competitions:
    cursor.execute(
        "INSERT OR IGNORE INTO Competitions (competition_id, competition_name, parent_id, type, gender, category_id) VALUES (?, ?, ?, ?, ?, ?)",
        (
            comp['id'],
            comp['name'],
            comp.get('parent_id'),
            comp.get('type'),
            comp.get('gender'),
            comp['category']['id']
        )
    )

conn.commit()
print("Data inserted successfully from API.")



Data inserted successfully from API.


In [ ]:
#executing all the sql queries
# 1) List all competitions along with their category name
cursor.execute("""
SELECT c.competition_id, c.competition_name, cat.category_name
FROM Competitions c
JOIN Categories cat ON c.category_id = cat.category_id;
""")
print("Competitions with Categories:\n", cursor.fetchall())

# 2) Count the number of competitions in each category
cursor.execute("""
SELECT cat.category_name, COUNT(c.competition_id)
FROM Competitions c
JOIN Categories cat ON c.category_id = cat.category_id
GROUP BY cat.category_name;
""")
print("Competition count per category:\n", cursor.fetchall())

# 3) Find all competitions of type 'doubles'
cursor.execute("SELECT competition_id, competition_name FROM Competitions WHERE type = 'doubles';")
print("Doubles competitions:\n", cursor.fetchall())

# 4) Competitions in a specific category (Hopman Cup)
cursor.execute("""
SELECT c.competition_id, c.competition_name
FROM Competitions c
JOIN Categories cat ON c.category_id = cat.category_id
WHERE cat.category_name = 'Hopman Cup';
""")
print("Competitions in Hopman Cup category:\n", cursor.fetchall())

# 5) Parent and Sub competitions
cursor.execute("""
SELECT p.competition_name AS parent, c.competition_name AS sub
FROM Competitions c
JOIN Competitions p ON c.parent_id = p.competition_id;
""")
print("Parent/Sub competitions:\n", cursor.fetchall())

# 6) Distribution of competition types by category
cursor.execute("""
SELECT cat.category_name, c.type, COUNT(*)
FROM Competitions c
JOIN Categories cat ON c.category_id = cat.category_id
GROUP BY cat.category_name, c.type;
""")
print("Distribution by type:\n", cursor.fetchall())

# 7) Competitions with no parent
cursor.execute("SELECT competition_id, competition_name FROM Competitions WHERE parent_id IS NULL;")
print("Top-level competitions:\n", cursor.fetchall())


Competitions with Categories:
 [('sr:competition:620', 'Hopman Cup', 'Hopman Cup'), ('sr:competition:660', 'World Team Cup', 'ATP'), ('sr:competition:990', 'ATP Challenger Tour Finals', 'Challenger'), ('sr:competition:1207', 'Championship International Series', 'WTA'), ('sr:competition:2100', 'Davis Cup', 'Davis Cup'), ('sr:competition:2102', 'Billie Jean King Cup', 'Billie Jean King Cup'), ('sr:competition:2555', 'Wimbledon Men Singles', 'ATP'), ('sr:competition:2557', 'Wimbledon Men Doubles', 'ATP'), ('sr:competition:2559', 'Wimbledon Women Singles', 'WTA'), ('sr:competition:2561', 'Wimbledon Women Doubles', 'WTA'), ('sr:competition:2563', 'Wimbledon Mixed Doubles', 'ATP'), ('sr:competition:2567', 'Australian Open Men Singles', 'ATP'), ('sr:competition:2569', 'Australian Open Men Doubles', 'ATP'), ('sr:competition:2571', 'Australian Open Women Singles', 'WTA'), ('sr:competition:2573', 'Australian Open Women Doubles', 'WTA'), ('sr:competition:2575', 'Australian Open Mixed Doubles', 'A

In [ ]:
# code for the second table
#importing the libraries
import requests

url = "https://api.sportradar.com/tennis/trial/v3/en/complexes.json"

headers = {
    "accept": "application/json",
    "x-api-key": "iaTuGgBk0r1GXdd3bIyvQOvEb5uYq0I7fmYiATOl"
}

response = requests.get(url, headers=headers)

print(response.text)
# convert JSON response into Python dictionary
data = json.loads(response.text)

# extract complexes
complexes = data['complexes']

complexes_list = []
venues_list = []

# loop through complexes
for compx in complexes:
    # complex details
    complexes_list.append({
        'complex_id': compx['id'],
        'complex_name': compx['name']
    })


    if 'venues' in compx:
        for venue in compx['venues']:
            venues_list.append({
                'venue_id': venue['id'],
                'venue_name': venue['name'],
                'city_name': venue.get('city_name'),
                'country_name': venue.get('country_name'),
                'country_code': venue.get('country_code'),
                'timezone': venue.get('timezone'),
                'complex_id': compx['id']
            })

# removing duplicates
unique_complexes = {frozenset(c.items()): c for c in complexes_list}.values()
unique_venues = {frozenset(v.items()): v for v in venues_list}.values()

# print for verification
print("Complexes List:")
for c in unique_complexes:
    print(c)

print("\nVenues List:")
for v in unique_venues:
    print(v)

#converting it into a datframe
complexes_df = pd.DataFrame(unique_complexes)
venues_df = pd.DataFrame(unique_venues)
#printing results
complexes_df.head()
venues_df.head()


{"generated_at":"2025-09-02T09:51:00+00:00","complexes":[{"id":"sr:complex:705","name":"Nacional","venues":[{"id":"sr:venue:70045","name":"Cancha Central","city_name":"Santiago","country_name":"Chile","country_code":"CHL","timezone":"America\/Santiago"}]},{"id":"sr:complex:1078","name":"Estadio de la Cartuja","venues":[{"id":"sr:venue:74856","name":"Centre Court","city_name":"Seville","country_name":"Spain","country_code":"ESP","timezone":"Europe\/Madrid"},{"id":"sr:venue:74858","name":"Court One","city_name":"Seville","country_name":"Spain","country_code":"ESP","timezone":"Europe\/Madrid"}]},{"id":"sr:complex:1495","name":"Sibur Arena","venues":[{"id":"sr:venue:1496","name":"Court 1","city_name":"Saint Petersburg","country_name":"Russia","country_code":"RUS","timezone":"Europe\/Moscow"},{"id":"sr:venue:1500","name":"CENTER COURT","city_name":"Saint Petersburg","country_name":"Russia","country_code":"RUS","timezone":"Europe\/Moscow"},{"id":"sr:venue:62149","name":"Sibur Arena","city_na

venue_id      venue_name         city_name country_name country_code  \
0  sr:venue:70045  Cancha Central          Santiago        Chile          CHL   
1  sr:venue:74856    Centre Court           Seville        Spain          ESP   
2  sr:venue:74858       Court One           Seville        Spain          ESP   
3   sr:venue:1496         Court 1  Saint Petersburg       Russia          RUS   
4   sr:venue:1500    CENTER COURT  Saint Petersburg       Russia          RUS   

           timezone       complex_id  
0  America/Santiago   sr:complex:705  
1     Europe/Madrid  sr:complex:1078  
2     Europe/Madrid  sr:complex:1078  
3     Europe/Moscow  sr:complex:1495  
4     Europe/Moscow  sr:complex:1495

In [ ]:
import sqlite3

# 3) creating tables
conn = sqlite3.connect(":memory:")
cur = conn.cursor()

cur.execute("""
CREATE TABLE Complexes (
  complex_id   VARCHAR(50) PRIMARY KEY,
  complex_name VARCHAR(100) NOT NULL
);
""")

cur.execute("""
CREATE TABLE Venues (
  venue_id     VARCHAR(50) PRIMARY KEY,
  venue_name   VARCHAR(100) NOT NULL,
  city_name    VARCHAR(100) NOT NULL,
  country_name VARCHAR(100) NOT NULL,
  country_code CHAR(3)      NOT NULL,
  timezone     VARCHAR(100) NOT NULL,
  complex_id   VARCHAR(50)  NOT NULL,
  FOREIGN KEY (complex_id) REFERENCES Complexes(complex_id)
);
""")

cur.executemany("INSERT OR IGNORE INTO Complexes VALUES (?,?)", complexes_rows)
cur.executemany("""
INSERT OR IGNORE INTO Venues
(venue_id, venue_name, city_name, country_name, country_code, timezone, complex_id)
VALUES (?,?,?,?,?,?,?)
""", venues_rows)
conn.commit()

# 4) executing the queries
def q(sql, params=()):
    cur.execute(sql, params)
    return cur.fetchall()

print("1)", q("""
SELECT v.venue_id, v.venue_name, c.complex_name
FROM Venues v JOIN Complexes c ON c.complex_id = v.complex_id
ORDER BY c.complex_name, v.venue_name
""")[:10])

print("2)", q("""
SELECT c.complex_name, COUNT(v.venue_id) AS venue_count
FROM Complexes c LEFT JOIN Venues v ON v.complex_id = c.complex_id
GROUP BY c.complex_id, c.complex_name
ORDER BY venue_count DESC, c.complex_name
""")[:10])

print("3)", q("""
SELECT venue_id, venue_name, city_name, timezone, complex_id
FROM Venues WHERE country_name = ?
""", ("Chile",)))

print("4)", q("SELECT venue_id, venue_name, timezone FROM Venues ORDER BY timezone, venue_name")[:10])

print("5)", q("""
SELECT c.complex_name, COUNT(v.venue_id) AS venue_count
FROM Complexes c JOIN Venues v ON v.complex_id = c.complex_id
GROUP BY c.complex_id, c.complex_name HAVING COUNT(v.venue_id) > 1
ORDER BY venue_count DESC
""")[:10])

print("6)", q("""
SELECT country_name, city_name, venue_name
FROM Venues ORDER BY country_name, city_name, venue_name
""")[:10])

print("7)", q("""
SELECT v.venue_id, v.venue_name, v.city_name, v.country_name, v.timezone
FROM Venues v JOIN Complexes c ON c.complex_id = v.complex_id
WHERE c.complex_name = ?
ORDER BY v.venue_name
""", ("Nacional",)))


1) [('sr:venue:14794', 'Center Court', 'A.S.D. Tennis Club Como'), ('sr:venue:14796', 'Court 1', 'A.S.D. Tennis Club Como'), ('sr:venue:14798', 'Court 2', 'A.S.D. Tennis Club Como'), ('sr:venue:83791', 'Court 3', 'A.S.D. Tennis Club Como'), ('sr:venue:33956', 'Court 5', 'A.S.D. Tennis Club Como'), ('sr:venue:33958', 'Indoor 1', 'A.S.D. Tennis Club Como'), ('sr:venue:33960', 'Indoor 2', 'A.S.D. Tennis Club Como'), ('sr:venue:83807', 'Indoor 4', 'A.S.D. Tennis Club Como'), ('sr:venue:83809', 'Indoor 5', 'A.S.D. Tennis Club Como'), ('sr:venue:73581', 'TC Giussano Indoors 3', 'A.S.D. Tennis Club Como')]
2) [('Buenos Aires Lawn Tennis Club', 30), ('Melbourne Park', 25), ('Hurd Tennis Center', 24), ('Club Tennis Las Terrazas de Miraflores', 22), ('Qi Zhong Tennis Center', 22), ('Ariake Tennis Forest Park Ariake Colesseum', 21), ('Indian Wells Tennis Garden', 21), ('Megasaray Tennis Academy', 21), ('AELTC Wimbledon Qualifying and Community Sports Centre', 20), ('Clube Hipico Santo Amaro', 20)

In [ ]:
# code for the third table
#importing the needed libraries
import requests
import json
import pandas as pd

url = "https://api.sportradar.com/tennis/trial/v3/en/double_competitors_rankings.json"

headers = {
    "accept": "application/json",
    "x-api-key": "iaTuGgBk0r1GXdd3bIyvQOvEb5uYq0I7fmYiATOl"
}

response = requests.get(url, headers=headers)

print(response.text)

# fetching response
response = requests.get(url, headers=headers)

# convert JSON response into Python dictionary
data = json.loads(response.text)

# extract complexes
complexes_list = []
venues_list = []

# loop through complexes
for compex in complexes:
    # complex details
    complexes_list.append({
        'complex_id': compx['id'],
        'complex_name': compx['name']
    })

    # venues linked to this complex
    if 'venues' in compx:
        for venue in compx['venues']:
            venues_list.append({
                'venue_id': venue['id'],
                'venue_name': venue['name'],
                'city_name': venue.get('city_name'),
                'country_name': venue.get('country_name'),
                'country_code': venue.get('country_code'),
                'timezone': venue.get('timezone'),
                'complex_id': compx['id']
            })

# converting to DataFrames
complexes_df = pd.DataFrame(complexes_list).drop_duplicates()
venues_df = pd.DataFrame(venues_list).drop_duplicates()

# display the result
print("Complexes DataFrame:")
display(complexes_df.head())

print("\nVenues DataFrame:")
display(venues_df.head())


{"generated_at":"2025-09-02T10:28:18+00:00","rankings":[{"type_id":2,"name":"ATP","year":2025,"week":36,"gender":"men","competitor_rankings":[{"rank":1,"movement":0,"points":8390,"competitions_played":26,"competitor":{"id":"sr:competitor:59131","name":"Glasspool, Lloyd","country":"Great Britain","country_code":"GBR","abbreviation":"GLA"}},{"rank":2,"movement":0,"points":7825,"competitions_played":27,"competitor":{"id":"sr:competitor:108099","name":"Cash, Julian","country":"Great Britain","country_code":"GBR","abbreviation":"CAS"}},{"rank":3,"movement":0,"points":7595,"competitions_played":21,"competitor":{"id":"sr:competitor:49363","name":"Pavic, Mate","country":"Croatia","country_code":"HRV","abbreviation":"PAV"}},{"rank":3,"movement":0,"points":7595,"competitions_played":21,"competitor":{"id":"sr:competitor:51836","name":"Arevalo-Gonzalez, Marcelo","country":"El Salvador","country_code":"SLV","abbreviation":"ARE"}},{"rank":5,"movement":0,"points":6330,"competitions_played":24,"compet

complex_id complex_name
0  sr:complex:83737  Queens Park


Venues DataFrame:


venue_id             venue_name  city_name country_name country_code  \
0  sr:venue:83739  Queens Park - Court 2  Southport    Australia          AUS   
1  sr:venue:83741  Queens Park - Court 6  Southport    Australia          AUS   
2  sr:venue:83743  Queens Park - Court 8  Southport    Australia          AUS   
3  sr:venue:83745  Queens Park - Court 1  Southport    Australia          AUS   
4  sr:venue:83747  Queens Park - Court 3  Southport    Australia          AUS   

             timezone        complex_id  
0  Australia/Brisbane  sr:complex:83737  
1  Australia/Brisbane  sr:complex:83737  
2  Australia/Brisbane  sr:complex:83737  
3  Australia/Brisbane  sr:complex:83737  
4  Australia/Brisbane  sr:complex:83737

In [ ]:
# 3) Creating tables
conn = sqlite3.connect(":memory:")
cur = conn.cursor()

cur.execute("""
CREATE TABLE Complexes (
  complex_id   VARCHAR(50) PRIMARY KEY,
  complex_name VARCHAR(100) NOT NULL
);
""")

cur.execute("""
CREATE TABLE Venues (
  venue_id     VARCHAR(50) PRIMARY KEY,
  venue_name   VARCHAR(100) NOT NULL,
  city_name    VARCHAR(100) NOT NULL,
  country_name VARCHAR(100) NOT NULL,
  country_code CHAR(3)      NOT NULL,
  timezone     VARCHAR(100) NOT NULL,
  complex_id   VARCHAR(50)  NOT NULL,
  FOREIGN KEY (complex_id) REFERENCES Complexes(complex_id)
);
""")

cur.executemany("INSERT OR IGNORE INTO Complexes VALUES (?,?)", complexes_rows)
cur.executemany("""
INSERT OR IGNORE INTO Venues
(venue_id, venue_name, city_name, country_name, country_code, timezone, complex_id)
VALUES (?,?,?,?,?,?,?)
""", venues_rows)
conn.commit()


# 5) executing the  queries
print("1) Venues with complex name:\n", q("""
SELECT v.venue_id, v.venue_name, c.complex_name
FROM Venues v JOIN Complexes c ON c.complex_id = v.complex_id
ORDER BY c.complex_name, v.venue_name
""")[:10])

print("\n2) Venue count per complex:\n", q("""
SELECT c.complex_name, COUNT(v.venue_id) AS venue_count
FROM Complexes c LEFT JOIN Venues v ON v.complex_id = c.complex_id
GROUP BY c.complex_id, c.complex_name
ORDER BY venue_count DESC, c.complex_name
""")[:10])

print("\n3) Venues in Chile:\n", q("""
SELECT venue_id, venue_name, city_name, timezone, complex_id
FROM Venues WHERE country_name = ?
""", ("Chile",)))

print("\n4) All venues with timezone:\n", q("""
SELECT venue_id, venue_name, timezone
FROM Venues ORDER BY timezone, venue_name
""")[:10])

print("\n5) Complexes with >1 venue:\n", q("""
SELECT c.complex_name, COUNT(v.venue_id) AS venue_count
FROM Complexes c JOIN Venues v ON v.complex_id = c.complex_id
GROUP BY c.complex_id, c.complex_name HAVING COUNT(v.venue_id) > 1
ORDER BY venue_count DESC
""")[:10])

print("\n6) Venues grouped by country:\n", q("""
SELECT country_name, city_name, venue_name
FROM Venues ORDER BY country_name, city_name, venue_name
""")[:10])

print("\n7) Venues for complex Nacional:\n", q("""
SELECT v.venue_id, v.venue_name, v.city_name, v.country_name, v.timezone
FROM Venues v JOIN Complexes c ON c.complex_id = v.complex_id
WHERE c.complex_name = ?
ORDER BY v.venue_name
""", ("Nacional",)))

1) Venues with complex name:
 [('sr:venue:14794', 'Center Court', 'A.S.D. Tennis Club Como'), ('sr:venue:14796', 'Court 1', 'A.S.D. Tennis Club Como'), ('sr:venue:14798', 'Court 2', 'A.S.D. Tennis Club Como'), ('sr:venue:83791', 'Court 3', 'A.S.D. Tennis Club Como'), ('sr:venue:33956', 'Court 5', 'A.S.D. Tennis Club Como'), ('sr:venue:33958', 'Indoor 1', 'A.S.D. Tennis Club Como'), ('sr:venue:33960', 'Indoor 2', 'A.S.D. Tennis Club Como'), ('sr:venue:83807', 'Indoor 4', 'A.S.D. Tennis Club Como'), ('sr:venue:83809', 'Indoor 5', 'A.S.D. Tennis Club Como'), ('sr:venue:73581', 'TC Giussano Indoors 3', 'A.S.D. Tennis Club Como')]

2) Venue count per complex:
 [('Buenos Aires Lawn Tennis Club', 30), ('Melbourne Park', 25), ('Hurd Tennis Center', 24), ('Club Tennis Las Terrazas de Miraflores', 22), ('Qi Zhong Tennis Center', 22), ('Ariake Tennis Forest Park Ariake Colesseum', 21), ('Indian Wells Tennis Garden', 21), ('Megasaray Tennis Academy', 21), ('AELTC Wimbledon Qualifying and Community